# Stalactite Formation

In [1012]:
%matplotlib osx 
# On Macs use osx

import numpy as np
from numpy.random import rand
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm

In [1014]:
def find_2D_gradient(A,x,y):
    g = 0
    if x < len(A)//2:
        while y-g >= 0 and A[x+1,y-g] ==1:
            g += 1
        return g
    else:
        while y-g >= 0 and A[x-1,y-g] == 1:
            g += 1
        return g
    
def find_3D_gradient(A,x,y):
    xx = x+1
    yy = y+1
    g = A[xx,yy]
    
    l = A[x+1,y]
    if (l > g):
        xx = x+1
        yy = y
        g = A[xx,yy]
    if A[x+1,y-1] > g:
        xx = x+1
        yy = y-1
        g = A[xx,yy]
    if A[x,y-1] > g:
        xx = x
        yy = y-1
        g = A[xx,yy]
    if A[x-1,y-1] > g:
        xx = x-1
        yy = y-1
        g = A[xx,yy]
    if A[x-1,y] > g:
        xx = x-1
        yy = y
        g = A[xx,yy]
    if A[x-1,y+1] > g:
        xx = x-1
        yy = y+1
        g = A[xx,yy]
    if A[x,y+1] > g:
        xx = x
        yy = y+1
        g = A[xx,yy]
    return xx, yy, g
              

In [1015]:
def AddHill(Z,NX,NY,xx,yy,r,h):
    
    for x in range(NX):
        for y in range(NY):
            dx = np.mod(x-xx+NX/2,NX)-NX/2; # difference i-i0 but apply p.b.c. 
            dy = np.mod(y-yy+NY/2,NY)-NY/2;
            dr = np.sqrt(dx**2+dy**2);
            if (dr<r):
                Z[x,y] += h * (np.cos(dr/r*np.pi/2.0))**2;
    
    return Z

In [1016]:
nParticles = 500
maxX = 70
maxY = 70

d  = 1 # grid spacing in meters
dx = d # keep dx=dy for simplicity
dy = d

LX=maxX*dx
LY=maxY*dy

A = np.zeros((maxX, maxY))

In [1017]:
# Set-up figure
def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

def update_figure():
        plt.clf()
        ax1 = fig.add_subplot(111,projection='3d')

        # use equal x-y aspect with an explicit vertical exageration
        vert_exag = 4.
        ax1.set_xlim3d(25,45)#max(maxX,maxY))
        ax1.set_ylim3d(25,45)#max(maxX,maxY))
        ax1.set_zlim3d(0,170)

        ZPlot = np.copy(A)
        ax1.plot_surface(X,Y,ZPlot, cmap = cm.copper, rstride=1, cstride=1,
                antialiased=False,linewidth=0)

        plt.axis('off')
        plt.draw()
        plt.pause(0.0001)

In [1019]:
from matplotlib.animation import FFMpegWriter
metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)

In [1020]:
def check_perimeter(A, r):
    #Check the perimeter around base of stalactite for particles
    a = np.sum(A[maxX//2 -r: maxX//2 +r+1, maxY//2+r] == 0)
    b = np.sum(A[maxX//2 -r: maxX//2 +r+1, maxY//2-r] == 0)
    c = np.sum(A[maxY//2 -r+1: maxY//2 +r, maxX//2+r] == 0)
    d = np.sum(A[maxY//2 -r+1: maxY//2 +r, maxX//2-r] == 0)
    return a+b+c+d == 0

In [1021]:
def deposit_center_droplet(A,xx,yy,r,h):
    #Deposit a ring around the center water source
    A = AddHill(A,maxX,maxY,xx+1,yy+1,r,h)
    A = AddHill(A,maxX,maxY,xx+1,yy  ,r,h)
    A = AddHill(A,maxX,maxY,xx+1,yy-1,r,h)
    A = AddHill(A,maxX,maxY,xx  ,yy-1,r,h)
    A = AddHill(A,maxX,maxY,xx-1,yy-1,r,h)
    A = AddHill(A,maxX,maxY,xx-1,yy  ,r,h)
    A = AddHill(A,maxX,maxY,xx-1,yy+1,r,h)
    A = AddHill(A,maxX,maxY,xx  ,yy+1,r,h)

In [1022]:
count = 0
zLimit = 150
p = .001 #evaporating probability
r = 1 #radius
h = 2 #height
z = 0
maxRadius = r*2
# Set up figure
fig = init_figure()

with writer.saving(fig, "Stalactite1.mp4", 200):
    deposit_center_droplet(A,maxX//2,maxY//2,r,h)
    for i in range(1,nParticles):
        s = np.random.random() #Used to choose between center water source and outer water source

        if z <= zLimit:
            if s < .4: 
                #Build Stalactite Straw
                xx = maxX//2
                yy = maxY//2
                k = np.random.random(); #drop doesn't always deposit
                if (k < .1):
                    deposit_center_droplet(A,xx,yy,r,h)
                    z += h

            elif i > 2:
                #Select an empty position along the perimeter of stalactite
                filled = True
                while filled: 
                    x  = np.random.randint(maxX//2 -maxRadius, maxX//2 +maxRadius+1)

                    if x-maxRadius == maxX//2 or x+maxRadius == maxX//2:
                        y  = np.random.randint(maxY//2 -maxRadius, maxY//2 +maxRadius+1)
                    else:
                        y  = np.random.choice([maxY//2 -maxRadius, maxY//2 +maxRadius])

                    filled = A[x,y] > 0

                while True:
                    count += 1
                    xOrg = x
                    yOrg = y

                    rr = np.random.random(); # Random float:  0.0 <= r < 1.0

                    gd = np.random.randint(40,71) #Effects the steepness of the stalactite
                    mv = np.random.random()
                    gd = gd/100
                    xx, yy, g = find_3D_gradient(A,x,y)
                    grad_p = -10**-(g/10) +1  #probablity of moving based on gradient

                    if (rr < grad_p):
                        if g <= A[x,y] + int(np.ceil(g*gd)):
                            x = xx
                            y = yy

                    if (x < 0):
                        x = maxX - 1
                    elif (x >= maxX):
                        x = 0  

                    xp = x + 1
                    if (xp >= maxX):
                        xp = 0

                    xm = x - 1
                    if (xm < 0):
                        xm = maxX - 1 

                    yp = y + 1
                    if (yp >= maxY):
                        yp = maxY-1
                    ym = y - 1

                    m = np.random.random(); 

                    n = sum([A[xp,y]>0,A[x,yp]>0,A[xm,y]>0,A[x,ym]>0,A[xp,yp]>0,A[xp,ym]>0,A[xm,ym]>0,A[xm,yp]>0])

                    if (n > 0 and m < p ): 
                        A = AddHill(A,maxX,maxY,x,y,r,h)

                        full = check_perimeter(A,maxRadius)
                        if full:
                            maxRadius +=r

                        break # particle was attached, break out of current loop and insert next one
                        

        if (np.mod(i,10)==0): 
            print(i,end='')
            fig.clear()
            ax = fig.gca(projection='3d')
            
            x = np.arange(maxX)
            y = np.arange(maxY)
            X,Y = np.meshgrid(y,x) 
            ZMaxOrg = np.max(A)
        
            ax.plot_surface(X, Y, A, cmap=cm.coolwarm, antialiased=False)
            update_figure()
            plt.pause(0.01)
            writer.grab_frame()
            
        else:
            print('.',end='')  
            
            
update_figure()

.........10.........20.........30.........40.........50.........60.........70.........80.........90.........100.........110.........120.........130.........140.........150.........160.........170.........180.........190.........200.........210.........220.........230.........240.........250.........260.........270.........280.........290.........300.........310.........320.........330.........340.........350.........360.........370.........380.........390.........400.........410.........420.........430.........440.........450.........460.........470.........480.........490.........